In [1]:
import datetime
import math
import time
import itertools
from contextlib import closing
from collections import OrderedDict
import json
import numpy as np
import pandas as pd
import MySQLdb
import pymssql
from sqlalchemy import create_engine
import dfutils

In [2]:
pd.set_option('display.max_rows', 1500)
pd.set_option('display.max_columns', 500)

In [3]:
def optimized_execute(query, commit=False):
    '''
    Executes the search query in Northpoint
    '''
    
    with closing(pymssql.connect(host='10.16.1.16', user='readonly_user', password='readonly_user',
                                 database='PnLAppDb')) as np_pnl_conn:
        with closing(np_pnl_conn.cursor()) as np_pnl_cursor:
            np_pnl_cursor.execute(query)
            if commit:
                np_pnl_conn.commit()
                return

            fetched_res = np_pnl_cursor.fetchall()  # fetch (and discard) remaining rows\
            return fetched_res

In [4]:
def get_position_calculated_values_history_max_date():  # done
    query = "SELECT MAX(PCVH.TradeDate) FROM [PnLAppDb].[dbo].[PositionCalculatedValuesHistory] AS PCVH "
    results = optimized_execute(query)
    if len(results) == 0:
        return None

    return results[0][0]

In [5]:
def get_position_calculated_values_history(start_date_yyyy_mm_dd=None, end_date_yyyy_mm_dd=None,
                                           limit_to_tradegroups=[], is_tg_names_in_tradar_format=False,
                                           fund_code=None, NP_qty_rollup=True):
    if start_date_yyyy_mm_dd is None or end_date_yyyy_mm_dd is None:
        start_date_yyyy_mm_dd = '2019-03-01'
        end_date_yyyy_mm_dd = get_position_calculated_values_history_max_date()
    tg_filter_clause = ""
    if len([tg for tg in limit_to_tradegroups if tg is not None]) > 0:
        tg_filter_clause = " AND PCVH.TradeGroup IN (" + ",".join([("'" + tg + "'") 
                                                                   for tg in limit_to_tradegroups 
                                                                   if tg is not None]) + ") "
        if is_tg_names_in_tradar_format: 
            tg_filter_clause = tg_filter_clause.replace('PCVH.TradeGroup', 'SUBSTRING(PCVH.TradeGroup,0,21)')
            
    fund_code_filtuer_clause = " " if fund_code is None else " AND PCVH.FundCode = '" + fund_code + "' "
    # region query
    # New Fund by added bv Kshitij "WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL":"MACO"
    query = "SELECT " \
            "PCVH.TradeDate, " \
            "ISNULL(PCVH.FundCode, " \
            "CASE F.FundName " \
            "WHEN 'Columbia' THEN 'CAM' " \
            "WHEN 'Litman Gregory' THEN 'LG' " \
            "WHEN 'The Arbitrage Credit Opportunities Fund' THEN 'TACO' " \
            "WHEN 'The Arbitrage Event-Driven Fund' THEN 'AED' " \
            "WHEN 'The Arbitrage Fund' THEN 'ARB' " \
            "WHEN 'TransAmerica' THEN 'TAF' " \
            "WHEN 'WIC Arbitrage Partners' THEN 'WIC' " \
            "WHEN 'The Arbitrage Tactical Equity Fund' THEN 'TAQ' " \
            "WHEN 'Water Island Event-Driven Fund' THEN 'WED' " \
            "WHEN 'Water Island Capital Lev Arb Fund' THEN 'WED' " \
            "WHEN 'WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL' THEN 'MACO' " \
            "WHEN 'Morningstar Alternatives Fund' THEN 'MALT' " \
            "END " \
            ") AS FundCode, " \
            "SPT_TRDGRP.SecName AS TradeGroup, " \
            "SPT_TRDGRP.SecName AS TradeGroup_Tradar_Name, " \
            "PCVH.[Marketing GROUP] AS Sleeve,   " \
            "ISNULL(PCVH.[Bucket],'NA') AS Bucket, " \
            "PCVH.TradeGroupId, " \
            "SPT.StandardTicker As Ticker, " \
            "SPT.BloombergGlobalId, " \
            "SPT.BloombergGID, " \
            "ISNULL(SPT.BloombergGlobalId,SPT.BloombergGID) AS BBGID, " \
            "SPT.SecType, " \
            "ISNULL(SPT.MarketCapCategory, 'N/A') AS MarketCapCategory, " \
            "PCVH.SecurityID, " \
            "PCVH.DealTermsCash, " \
            "PCVH.DealTermsStock, " \
            "PCVH.DealValue, " \
            "PCVH.DealClosingDate, " \
            "CASE " \
            "WHEN SPT.SecType = 'FxFwd' THEN 0.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Equity Special Situations'  THEN 1.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Opportunistic'  THEN 1.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Merger Arbitrage'  THEN " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') THEN " \
            "CASE PCVH.DealValue WHEN 0 THEN 0.0 ELSE PCVH.DealTermsStock/PCVH.DealValue END " \
            "ELSE 1.0 END " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Credit Opportunities'  THEN " \
            "CASE WHEN SPT.SecType IN ('EQ','ExchOpt') THEN 1.0 ELSE 0.0 END " \
            "ELSE NULL END " \
            "AS [Equity Risk Factor], " \
            "PCVH.DV_01, " \
            "PCVH.CR_01, " \
            "PCVH.Adj_CR_01, " \
            "ISNULL(SPT.UltimateCountry,'N/A') AS UltimateCountry, " \
            "ISNULL(PCVH.AlphaHedge,'NA') AS AlphaHedge, " \
            "SUM(PCVH.ExposureLong_USD) AS Exposure_Long, " \
            "SUM(PCVH.ExposureShort_USD) AS Exposure_Short, " \
            "SUM(PCVH.ExposureLong_USD+PCVH.ExposureShort_USD) AS Exposure_Net, " \
            "CASE WHEN NAV.NAV = 0 THEN NULL " \
            "ELSE 100.0*(SUM(PCVH.ExposureLong_USD+PCVH.ExposureShort_USD)/NAV.NAV) END " \
            "AS [Exposure_Net(%)], " \
            "SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD) AS NetMktVal, " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') " \
            "THEN ABS(SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD)) ELSE NULL END AS Capital, " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') " \
            "THEN 100.0*(ABS(SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD))/NAV.NAV) ELSE NULL " \
            "END AS [Capital % of NAV], " \
            "100.0*SUM(PCVH.Base_Case_NAV_Impact) AS BaseCaseNavImpact, " \
            "100.0*SUM(PCVH.Outlier_NAV_Impact) AS OutlierNavImpact, " \
            "SUM(PCVH.Qty) AS QTY, " \
            "ISNULL(PCVH.TradeGroupLongShortFlag,'NA') AS LongShort, " \
            "ISNULL(SPT.GICSSectorName,'NA') AS Sector, " \
            "ISNULL(SPT.GICSIndustryName,'NA') AS Industry, " \
            "ISNULL(PCVH.TradeGroupCatalystRating, 'NA') AS CatalystRating, " \
            "CASE ISNULL(PCVH.TradeGroupCatalystRating, 'NA') " \
            "   WHEN 'NA' THEN 'N/A' " \
            "   WHEN 0 THEN 'No Catalyst' " \
            "   WHEN 1 THEN 'Soft' " \
            "   WHEN 2 THEN 'Binary' " \
            "   WHEN 3 THEN 'Hard' " \
            "   ELSE 'Unknown' END AS CatalystName, " \
            "NAV.NAV " \
            "FROM [PnLAppDb].[dbo].[PositionCalculatedValuesHistory] AS PCVH " \
            "INNER JOIN PnLAppDb.dbo.Funds AS F ON PCVH.Portfolio = F.FundID " \
            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT ON PCVH.SecurityID = SPT.ID " \
            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT_TRDGRP ON PCVH.TradeGroupId = SPT_TRDGRP.ID " \
            "LEFT OUTER JOIN PnLAppDb.pnl.DailyNAV AS NAV ON PCVH.Portfolio = NAV.FundId " \
            "AND PCVH.TradeDate = NAV.[DATE] " \
            "WHERE  TradeDate >= '" + start_date_yyyy_mm_dd + "' AND TradeDate <= '" + end_date_yyyy_mm_dd + "' " \
            + tg_filter_clause + \
            fund_code_filtuer_clause + \
            " AND PCVH.Qty <> 0 " \
            "GROUP BY " \
            "F.FundName, PCVH.FundCode,PCVH.TradeDate, PCVH.[Marketing GROUP], SPT_TRDGRP.SecName, " \
            "PCVH.TradeGroupId, SPT.StandardTicker, SPT.BloombergGlobalId, SPT.BloombergGID, " \
            "SPT.SecType, ISNULL(SPT.MarketCapCategory, 'N/A'), " \
            "PCVH.SecurityId, SPT.UltimateCountry, " \
            "ISNULL(PCVH.AlphaHedge,'NA'),PCVH.TradeGroupLongShortFlag, ISNULL(SPT.GICSSectorName,'NA'), " \
            "ISNULL(SPT.GICSIndustryName,'NA'), ISNULL(PCVH.TradeGroupCatalystRating, 'NA'), " \
            "ISNULL(PCVH.[Bucket],'NA'), PCVH.DealTermsCash, PCVH.DealTermsStock, " \
            "PCVH.DealValue, PCVH.DealClosingDate, " \
            "PCVH.DV_01, PCVH.CR_01, PCVH.Adj_CR_01, NAV.NAV, PCVH.Analyst " \
            "ORDER BY PCVH.TradeDate "
    # endregion
    results = optimized_execute(query)
    df = pd.DataFrame(results, columns=["Date", "FundCode", "TradeGroup", "TradeGroup_Tradar_Name", "Sleeve",
                                        "Bucket", "TradeGroupId", "Ticker", "BloombergGlobalId", "BloombergGID", "BBGID", "SecType", "MarketCapCategory",
                                        "SecurityId", "DealTermsCash", "DealTermsStock", "DealValue", 
                                        "DealClosingDate", "Equity_Risk_Factor", "DV01", "CR01", "Adj_CR01",
                                        "UltimateCountry", "AlphaHedge", "Exposure_Long", "Exposure_Short",
                                        "Exposure_Net", "Exposure_Net(%)", "NetMktVal", "Capital($)", 
                                        "Capital(%)", "BaseCaseNavImpact", "OutlierNavImpact", "Qty", 
                                        "LongShort", "Sector", "Industry", "CatalystRating", "CatalystName", "Fund_NAV"])

    float_cols = ['NetMktVal', 'Capital($)', 'Capital(%)', 'Exposure_Net', 'Exposure_Net(%)', 'BaseCaseNavImpact']
    df[float_cols] = df[float_cols].astype(float)
    df['Equity_Risk_Exp'] = df['Equity_Risk_Factor'].astype(float)*df['Exposure_Net'].astype(float)
    df[['DV01', 'CR01', 'Adj_CR01']] = df[['DV01', 'CR01', 'Adj_CR01']].fillna(0).astype(float)
    df["Date"] = df["Date"].apply(lambda x: pd.to_datetime(x))
    df["DealClosingDate"] = df["DealClosingDate"].apply(lambda x: pd.to_datetime(x))

    as_of_dt = datetime.datetime.strptime(end_date_yyyy_mm_dd, '%Y-%m-%d')

    def duration_calc(days):
        if days <= 90:
            return '0M-3M'
        if days <= 180:
            return '3M-6M'
        if days <= 365:
            return '6M-12M'
        return 'Yr+'

    df["DealDuration"] = df["DealClosingDate"].apply(lambda x: None if pd.isnull(x) else
                                                     duration_calc((as_of_dt - pd.to_datetime(x)).days))

    # region ADJUSTING FOR POSTED TRADES AFTER TRADE DATE - AFFECTING QTY ONLY
    # adjust for end_date_yyyy_mm_dd - take trades with tradedate = end_date_yyyy_mm_dd and posted_date
    #AFTER end_date_yyyy_mm_dd
    # adjust the Qty into the pcvh_df
    if NP_qty_rollup:
        qty_adjust_query = "SELECT " \
                            "A.TradeDate AS [DATE], " \
                            "CASE A.Fund " \
                            "WHEN 'Columbia' THEN 'CAM' " \
                            "WHEN 'Litman Gregory' THEN 'LG' " \
                            "WHEN 'The Arbitrage Credit Opportunities Fund' THEN 'TACO' " \
                            "WHEN 'The Arbitrage Event-Driven Fund' THEN 'AED' " \
                            "WHEN 'The Arbitrage Fund' THEN 'ARB' " \
                            "WHEN 'TransAmerica' THEN 'TAF' " \
                            "WHEN 'WIC Arbitrage Partners' THEN 'WIC' " \
                            "WHEN 'The Arbitrage Tactical Equity Fund' THEN 'TAQ' " \
                            "WHEN 'Water Island Event-Driven Fund' THEN 'WED' " \
                            "WHEN 'Water Island Capital Lev Arb Fund' THEN 'LEV' " \
                            "WHEN 'WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL COMMINGLED MASTER FUND LP' THEN 'MACO' " \
                            "WHEN 'Morningstar Alternatives Fund' THEN 'MALT' " \
                            "END AS FundCode, " \
                            "A.TradeGroupId, " \
                            "A.SecurityId, " \
                            "SUM((CASE SPT.SecType WHEN 'ExchOpt' THEN 100.0 ELSE 1.0 END)*A.Shares) AS Qty " \
                            "FROM " \
                            "[PnLAppDb].[dbo].[vTradesFlatView] AS A " \
                            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT ON A.SecurityId = SPT.ID " \
                            "WHERE PostedDate >= DATEADD(DAY,1,TradeDate) AND TradeDate >= '" \
                            + start_date_yyyy_mm_dd + "' " \
                            "GROUP BY A.TradeDate, A.SecurityId, A.Ticker, A.Fund, A.TradeGroupId, SPT.SecType "
        results = optimized_execute(qty_adjust_query)
        qty_adjust_df = pd.DataFrame(results, columns=['Date', 'FundCode', 'TradeGroupId', 'SecurityId', 'Qty_adj'])
        qty_adjust_df[['TradeGroupId', 'SecurityId', 'Qty_adj']] = qty_adjust_df[['TradeGroupId',
                                                                                  'SecurityId', 'Qty_adj']].astype(float)
        qty_adjust_df['Date'] = qty_adjust_df['Date'].apply(lambda x: pd.to_datetime(x))

        df[['TradeGroupId', 'SecurityId', 'Qty']] = df[['TradeGroupId', 'SecurityId', 'Qty']].astype(float)
        df = pd.merge(df, qty_adjust_df, how='left', on=['Date', 'FundCode', 'TradeGroupId', 'SecurityId'])
        df['Qty'] = df['Qty'] + df['Qty_adj'].fillna(0)
        del df['Qty_adj']
    # endregion
    print('PCVH retrieval completed....')
    return df

In [7]:
PCVH = get_position_calculated_values_history(start_date_yyyy_mm_dd='2019-05-02', end_date_yyyy_mm_dd='2019-05-02')

PCVH retrieval completed....


In [24]:
PCVH['TradeGroup'] = PCVH['TradeGroup'].apply(lambda x: x.upper())
PCVH['Date'] = PCVH['Date'].apply(lambda x: x.strftime('%Y-%m-%d'))

In [9]:
PCVH = PCVH[PCVH.SecType != 'FxFwd']

In [10]:
df_flat_file = pd.read_csv('C:/Users/aduprey/Desktop/COMBINED_5_02.csv')

In [11]:
df_flat_file['TradeGroup'] = df_flat_file['TradeGroup'].apply(lambda x: x.upper())

In [12]:
df_flat_file

Unnamed: 0        Date FundCode                      TradeGroup  \
0              0  2019-05-02      AED                  AABA R/R SHORT   
1              1  2019-05-02      AED                  AABA R/R SHORT   
2              2  2019-05-02      CAM                  AABA R/R SHORT   
3              3  2019-05-02      CAM                  AABA R/R SHORT   
4              4  2019-05-02       LG                  AABA R/R SHORT   
5              5  2019-05-02       LG                  AABA R/R SHORT   
6              6  2019-05-02      TAQ                  AABA R/R SHORT   
7              7  2019-05-02      TAQ                  AABA R/R SHORT   
8              8  2019-05-02      WED                  AABA R/R SHORT   
9              9  2019-05-02      WED                  AABA R/R SHORT   
10            10  2019-05-02      TAQ                        ACOR R/R   
11            11  2019-05-02      TAQ                        ACOR R/R   
12            12  2019-05-02      TAQ                        ACOR R/R   
13            13  2019-05-02      TAQ                        ACOR R/R   
14            14  2019-05-02      AED                       ADSW - WM   
15            15  2019-05-02      ARB                       ADSW - WM   
16            16  2019-05-02      CAM                       ADSW - WM   
17            17  2019-05-02      LEV                       ADSW - WM   
18            18  2019-05-02       LG                       ADSW - WM   
19            19  2019-05-02     MACO                       ADSW - WM   
20            20  2019-05-02     MALT                       ADSW - WM   
21            21  2019-05-02      ARB                           AEDNX   
22            22  2019-05-02      TAQ                        AIMC R/R   
23            23  2019-05-02      TAQ                        AIMC R/R   
24            24  2019-05-02      TAQ                        AIMC R/R   
25            25  2019-05-02      TAQ                        AIMC R/R   
26            26  2019-05-02      TAQ                        AIMC R/R   
27            27  2019-05-02      AED                   ALV R/R SHORT   
28            28  2019-05-02      AED                   ALV R/R SHORT   
29            29  2019-05-02      AED                   ALV R/R SHORT   
30            30  2019-05-02      AED                   ALV R/R SHORT   
31            31  2019-05-02      AED                   ALV R/R SHORT   
32            32  2019-05-02      CAM                   ALV R/R SHORT   
33            33  2019-05-02      CAM                   ALV R/R SHORT   
34            34  2019-05-02      CAM                   ALV R/R SHORT   
35            35  2019-05-02      CAM                   ALV R/R SHORT   
36            36  2019-05-02      CAM                   ALV R/R SHORT   
37            37  2019-05-02       LG                   ALV R/R SHORT   
38            38  2019-05-02       LG                   ALV R/R SHORT   
39            39  2019-05-02       LG                   ALV R/R SHORT   
40            40  2019-05-02       LG                   ALV R/R SHORT   
41            41  2019-05-02       LG                   ALV R/R SHORT   
42            42  2019-05-02      TAQ                   ALV R/R SHORT   
43            43  2019-05-02      TAQ                   ALV R/R SHORT   
44            44  2019-05-02      TAQ                   ALV R/R SHORT   
45            45  2019-05-02      TAQ                   ALV R/R SHORT   
46            46  2019-05-02      TAQ                   ALV R/R SHORT   
47            47  2019-05-02      WED                   ALV R/R SHORT   
48            48  2019-05-02      WED                   ALV R/R SHORT   
49            49  2019-05-02      WED                   ALV R/R SHORT   
50            50  2019-05-02      WED                   ALV R/R SHORT   
51            51  2019-05-02      WED                   ALV R/R SHORT   
52            52  2019-05-02      AED                       APC - CVX   
53            53  2019-05-02      AED                       APC 

In [13]:
df_flat_file = df_flat_file[df_flat_file.SecType != 'FXFWD']

In [14]:
df_flat_file = df_flat_file[df_flat_file.FundCode != 'ETF1']
df_flat_file = df_flat_file[df_flat_file.FundCode != 'ETF2']
df_flat_file = df_flat_file[df_flat_file.FundCode != 'INDEX1']
df_flat_file = df_flat_file[df_flat_file.FundCode != 'INDEX2']

In [15]:
#PCVH['Date'] = PCVH['Date'].apply(lambda x: x.strftime('%Y-%m-%d'))

In [16]:
print(len(PCVH))
print(len(df_flat_file))

1136
1131


In [32]:
pcvh = PCVH[PCVH.FundCode == 'AED']
f = df_flat_file[df_flat_file.FundCode == 'AED']

In [33]:
resulting = pd.merge(pcvh, f, how = 'outer', on=['Date', 'FundCode', 'TradeGroup', 'Ticker'])
resulting.columns

Index([u'Date', u'FundCode', u'TradeGroup', u'TradeGroup_Tradar_Name_x',
       u'Sleeve_x', u'Bucket_x', u'TradeGroupId_x', u'Ticker',
       u'BloombergGlobalId_x', u'BloombergGID_x', u'BBGID_x', u'SecType_x',
       u'MarketCapCategory_x', u'SecurityId_x', u'DealTermsCash_x',
       u'DealTermsStock_x', u'DealValue_x', u'DealClosingDate_x',
       u'Equity_Risk_Factor_x', u'DV01_x', u'CR01_x', u'Adj_CR01_x',
       u'UltimateCountry_x', u'AlphaHedge_x', u'Exposure_Long_x',
       u'Exposure_Short_x', u'Exposure_Net_x', u'Exposure_Net(%)_x',
       u'NetMktVal_x', u'Capital($)_x', u'Capital(%)_x',
       u'BaseCaseNavImpact_x', u'OutlierNavImpact_x', u'Qty_x', u'LongShort_x',
       u'Sector_x', u'Industry_x', u'CatalystRating_x', u'CatalystName_x',
       u'Fund_NAV_x', u'Equity_Risk_Exp_x', u'DealDuration_x', u'Unnamed: 0',
       u'TradeGroup_Tradar_Name_y', u'Sleeve_y', u'Bucket_y',
       u'TradeGroupId_y', u'BloombergGlobalId_y', u'BloombergGID_y',
       u'BBGID_y', u'SecType_

In [34]:
cols = ['Date', 'FundCode', 'TradeGroup', 'Ticker', 'TradeGroup_Tradar_Name_x', 'TradeGroup_Tradar_Name_y',
       'Sleeve_x', 'Sleeve_y', 'Bucket_x', 'Bucket_y', 'TradeGroupId_x', 'TradeGroupId_y',
       'BloombergGlobalId_x', 'BloombergGlobalId_y', 'BloombergGID_x', 'BloombergGID_y', 'BBGID_x', 'BBGID_y', 'SecType_x', 'SecType_y',
       'MarketCapCategory_x', 'MarketCapCategory_y', 'SecurityId_x', 'SecurityId_y', 'DealTermsCash_x', 'DealTermsCash_y',
       'DealTermsStock_x', 'DealTermsStock_y', 'DealValue_x', 'DealValue_y', 'DealClosingDate_x', 'DealClosingDate_y',
       'Equity_Risk_Factor_x', 'Equity_Risk_Factor_y', 'DV01_x', 'DV01_y', 'CR01_x', 'CR01_y', 'Adj_CR01_x', 'Adj_CR01_y',
       'UltimateCountry_x', 'UltimateCountry_y', 'AlphaHedge_x', 'AlphaHedge_y', 'Exposure_Long_x', 'Exposure_Long_y',
       'Exposure_Short_x', 'Exposure_Short_y', 'Exposure_Net_x', 'Exposure_Net_y', 'Exposure_Net(%)_x', 'Exposure_Net(%)_y',
       'NetMktVal_x', 'NetMktVal_y', 'Capital($)_x', 'Capital($)_y', 'Capital(%)_x', 'Capital(%)_y',
       'BaseCaseNavImpact_x', 'BaseCaseNavImpact_y', 'OutlierNavImpact_x', 'OutlierNavImpact_y', 'Qty_x', 'Qty_y', 'LongShort_x',
       'LongShort_y', 'Sector_x', 'Sector_y', 'Industry_x', 'Industry_y', 'CatalystRating_x', 'CatalystRating_y', 'CatalystName_x',
       'CatalystName_y', 'Fund_NAV_x', 'Fund_NAV_y', 'Equity_Risk_Exp_x', 'Equity_Risk_Exp_y', 'DealDuration_x', 'DealDuration_y']

In [35]:
r = resulting[cols]
r.sort_values(by=['TradeGroup'])

Date FundCode                      TradeGroup  \
151  2019-05-02      AED                  AABA R/R SHORT   
95   2019-05-02      AED                  AABA R/R SHORT   
16   2019-05-02      AED                       ADSW - WM   
81   2019-05-02      AED                   ALV R/R SHORT   
107  2019-05-02      AED                   ALV R/R SHORT   
46   2019-05-02      AED                   ALV R/R SHORT   
84   2019-05-02      AED                   ALV R/R SHORT   
85   2019-05-02      AED                   ALV R/R SHORT   
117  2019-05-02      AED                       APC - CVX   
30   2019-05-02      AED                       APC - CVX   
15   2019-05-02      AED                       APC - CVX   
105  2019-05-02      AED                       APC - CVX   
24   2019-05-02      AED                       APC - CVX   
147  2019-05-02      AED                       APC - CVX   
99   2019-05-02      AED                       APC - CVX   
144  2019-05-02      AED                       APU - UGI   
131  2019-05-02      AED                       APU - UGI   
156  2019-05-02      AED                   ARNC CONVERTS   
64   2019-05-02      AED                   ARNC CONVERTS   
70   2019-05-02      AED                        AVYA R/R   
29   2019-05-02      AED            BRSS - WIELAND GROUP   
39   2019-05-02      AED                       CBSTZ S/S   
51   2019-05-02      AED                      CELG - BMY   
37   2019-05-02      AED                      CELG - BMY   
152  2019-05-02      AED                      CELG - BMY   
134  2019-05-02      AED                        CNDT R/R   
32   2019-05-02      AED                         CSX R/R   
83   2019-05-02      AED                         CSX R/R   
108  2019-05-02      AED                  DLTR R/R SHORT   
94   2019-05-02      AED                  DLTR R/R SHORT   
122  2019-05-02      AED                  DLTR R/R SHORT   
75   2019-05-02      AED                  DLTR R/R SHORT   
126  2019-05-02      AED                 DNA FH - TEL NO   
133  2019-05-02      AED                  DOLE - MURDOCK   
40   2019-05-02      AED                   DOV R/R SHORT   
73   2019-05-02      AED                   DOV R/R SHORT   
18   2019-05-02      AED                   DOV R/R SHORT   
109  2019-05-02      AED                   DOW R/R SHORT   
87   2019-05-02      AED                   DOW R/R SHORT   
61   2019-05-02      AED                   DOW R/R SHORT   
130  2019-05-02      AED                   DOW R/R SHORT   
100  2019-05-02      AED                   DOW R/R SHORT   
65   2019-05-02      AED                         DXC R/R   
6    2019-05-02      AED                         DXC R/R   
47   2019-05-02      AED                         DXC R/R   
112  2019-05-02      AED                         DXC R/R   
155  2019-05-02      AED            EFII - SIRIS CAPITAL   
115  2019-05-02      AED                         ESI R/R   
142  2019-05-02      AED                         ESI R/R   
19   2019-05-02      AED                      FDC - FISV   
14   2019-05-02      AED                      FDC - FISV   
63   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
79   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
26   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
53   2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
149  2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
72   2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
49   2019-05-02      AED                      FOXA - DIS   
25   2019-05-02      AED                    GME SPEC M&A   
157  2019-05-02      AED                    GME SPEC M&A   
113  2019-05-02      AED                    GME SPEC M&A   
101  2019-05-02      AED                        HF - JLL   
138  2019-05-02      AED                        HF - JLL   
0    2019-05-02      AED                         HRI R/R   
33   2019-05-02      AED                         HRI R/R   
12   2019-05-02      AED                         HR

In [36]:
len(r)

165

In [37]:
t = r[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Exposure_Net_x', 'Exposure_Net_y', 'Capital($)_x', "Capital($)_y", 'DealValue_x', 'DealValue_y']]#, "Qty_x", "Qty_y"]]
t = t.sort_values(by='TradeGroup').round(2) #"DealTermsCash_x", 'DealTermsCash_y', 'DealTermsStock_x', 'DealTermsStock_y', 'DealValue_x', 'DealValue_y',
#t['Capital($)_x'] = t['Capital($)_x'].round()
#t['cap_T/F'] = t['Capital($)_x'] == t['Capital($)_y']
#t['dv01_T/F'] = t['DV01_x'] == t['DV01_y']
#t['cr01_T/F'] = t['CR01_x'] == t['CR01_y']
#t['adcr_T/F'] = t['Adj_CR01_x'] == t['Adj_CR01_y']
t['exp_T/F'] = abs((t['Exposure_Net_x']-t['Exposure_Net_y'])/(t['Exposure_Net_y'])) <= 0.05
#t['dc_T/F'] = abs((t['DealTermsCash_x'].astype(float)-t['DealTermsCash_y'])/(t['DealTermsCash_y'])) <= 0.01
#t['ds_T/F'] = abs((t['DealTermsStock_x'].astype(float)-t['DealTermsStock_y'])/(t['DealTermsStock_y'])) <= 0.01
t['dv_T/F'] = abs((t['DealValue_x'].astype(float)-t['DealValue_y'])/(t['DealValue_y'])) <= 0.01
t['cap_T/F'] = abs((t['Capital($)_x']-t['Capital($)_y'])/(t['Capital($)_y'])) <= 0.01
#t['qty_T/F'] = t['Qty_x'] == t['Qty_y']
#t = t[(t['cap_T/F'] == False)|(t['exp_T/F'] == False)]
t = t[(t['exp_T/F'] == False)|(t['cap_T/F'] == False)|(t['dv_T/F'] == False)]

In [38]:
t.sort_values(by='TradeGroup')

Date FundCode                      TradeGroup  \
151  2019-05-02      AED                  AABA R/R SHORT   
95   2019-05-02      AED                  AABA R/R SHORT   
81   2019-05-02      AED                   ALV R/R SHORT   
107  2019-05-02      AED                   ALV R/R SHORT   
46   2019-05-02      AED                   ALV R/R SHORT   
84   2019-05-02      AED                   ALV R/R SHORT   
85   2019-05-02      AED                   ALV R/R SHORT   
30   2019-05-02      AED                       APC - CVX   
15   2019-05-02      AED                       APC - CVX   
147  2019-05-02      AED                       APC - CVX   
99   2019-05-02      AED                       APC - CVX   
131  2019-05-02      AED                       APU - UGI   
156  2019-05-02      AED                   ARNC CONVERTS   
64   2019-05-02      AED                   ARNC CONVERTS   
70   2019-05-02      AED                        AVYA R/R   
39   2019-05-02      AED                       CBSTZ S/S   
51   2019-05-02      AED                      CELG - BMY   
37   2019-05-02      AED                      CELG - BMY   
152  2019-05-02      AED                      CELG - BMY   
134  2019-05-02      AED                        CNDT R/R   
32   2019-05-02      AED                         CSX R/R   
83   2019-05-02      AED                         CSX R/R   
108  2019-05-02      AED                  DLTR R/R SHORT   
94   2019-05-02      AED                  DLTR R/R SHORT   
122  2019-05-02      AED                  DLTR R/R SHORT   
75   2019-05-02      AED                  DLTR R/R SHORT   
40   2019-05-02      AED                   DOV R/R SHORT   
73   2019-05-02      AED                   DOV R/R SHORT   
18   2019-05-02      AED                   DOV R/R SHORT   
100  2019-05-02      AED                   DOW R/R SHORT   
61   2019-05-02      AED                   DOW R/R SHORT   
130  2019-05-02      AED                   DOW R/R SHORT   
87   2019-05-02      AED                   DOW R/R SHORT   
109  2019-05-02      AED                   DOW R/R SHORT   
65   2019-05-02      AED                         DXC R/R   
6    2019-05-02      AED                         DXC R/R   
47   2019-05-02      AED                         DXC R/R   
112  2019-05-02      AED                         DXC R/R   
115  2019-05-02      AED                         ESI R/R   
142  2019-05-02      AED                         ESI R/R   
14   2019-05-02      AED                      FDC - FISV   
63   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
79   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
26   2019-05-02      AED  FDC 5.00 01/15/24 MERGER BONDS   
53   2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
149  2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
72   2019-05-02      AED  FDC 5.75 01/15/24 MERGER BONDS   
49   2019-05-02      AED                      FOXA - DIS   
113  2019-05-02      AED                    GME SPEC M&A   
25   2019-05-02      AED                    GME SPEC M&A   
157  2019-05-02      AED                    GME SPEC M&A   
101  2019-05-02      AED                        HF - JLL   
0    2019-05-02      AED                         HRI R/R   
33   2019-05-02      AED                         HRI R/R   
12   2019-05-02      AED                         HRI R/R   
71   2019-05-02      AED                         HRI R/R   
102  2019-05-02      AED     ISAT LN - APAX & CONSORTIUM   
28   2019-05-02      AED                 JACFIN SPEC M&A   
80   2019-05-02      AED                      KD8 GY S/S   
58   2019-05-02      AED               LABL MERGER BONDS   
103  2019-05-02      AED               LABL MERGER BONDS   
158  2019-05-02      AED               LABL MERGER BONDS   
82   2019-05-02      AED               LABL MERGER BONDS   
137  2019-05-02      AED                    LEXEA - EXPE   
76   2019-05-02      AED                        LOGM R/R   
68   2019-05-02      AED                        LOG

In [33]:
PCVH[(PCVH.TradeGroup == 'DNA FH - TEL NO')&(PCVH.FundCode == 'ARB')].sort_values(by=['FundCode', 'Ticker'])

Date FundCode       TradeGroup TradeGroup_Tradar_Name  \
886   2019-04-30      ARB  DNA FH - TEL NO        DNA FH - TEL NO   
1146  2019-04-30      ARB  DNA FH - TEL NO        DNA FH - TEL NO   

                Sleeve     Bucket  TradeGroupId                 Ticker  \
886   Merger Arbitrage  Optimized       94708.0                 DNA FH   
1146  Merger Arbitrage  Optimized       94708.0  EUR/USD 6/14/2019 BBG   

     BloombergGlobalId  BloombergGID         BBGID SecType MarketCapCategory  \
886       BBG00F36XPQ9  BBG00F36XPQ9  BBG00F36XPQ9      EQ           Mid Cap   
1146              None          None          None   FxFwd               N/A   

      SecurityId DealTermsCash DealTermsStock DealValue DealClosingDate  \
886      94706.0       20.9000         0.0000   20.9000      2019-08-30   
1146     94581.0       20.9000         0.0000   20.9000      2019-08-30   

     Equity_Risk_Factor  DV01  CR01  Adj_CR01 UltimateCountry AlphaHedge  \
886               0E-13   0.0   0.0       0.0              FI      Alpha   
1146              0E-13   0.0   0.0       0.0             N/A      Hedge   

           Exposure_Long Exposure_Short  Exposure_Net  Exposure_Net(%)  \
886   4320362.7487000000          0E-10  4.320363e+06           0.2459   
1146               0E-10          0E-10  0.000000e+00           0.0000   

         NetMktVal    Capital($)  Capital(%)  BaseCaseNavImpact  \
886   4.320363e+06  4.320363e+06      0.2459                0.0   
1146 -8.504538e+06           NaN         NaN                0.0   

     OutlierNavImpact         Qty LongShort                  Sector  \
886           0.00000   181525.00      Long  Communication Services   
1146          0.00000 -3793881.99      Long                      NA   

                           Industry CatalystRating CatalystName  \
886   Diversified Telecommunication              1         Soft   
1146                             NA              1         Soft   

               Fund_NAV  Equity_Risk_Exp DealDuration  
886   1756693923.770000              0.0        0M-3M  
1146  1756693923.770000              0.0        0M-3M

In [32]:
df_flat_file[(df_flat_file.TradeGroup == 'DNA FH - TEL NO')&(df_flat_file.FundCode == 'ARB')].sort_values(by=['FundCode', 'Ticker'])

Unnamed: 0        Date FundCode       TradeGroup TradeGroup_Tradar_Name  \
240         240  2019-04-30      ARB  DNA FH - TEL NO        DNA FH - TEL NO   

               Sleeve     Bucket  TradeGroupId  Ticker BloombergGlobalId  \
240  Merger Arbitrage  Optimized             1  DNA FH      BBG00F36XPQ9   

     BloombergGID         BBGID SecType MarketCapCategory  SecurityId  \
240  BBG00F36XPQ9  BBG00F36XPQ9      EQ           Mid Cap         NaN   

     DealTermsCash  DealTermsStock  DealValue DealClosingDate  \
240           20.9             0.0       20.9      2019-08-30   

     Equity_Risk_Factor  DV01  CR01  Adj_CR01 UltimateCountry AlphaHedge  \
240                 0.0   0.0   0.0       0.0              FI      Alpha   

     Exposure_Long  Exposure_Short  Exposure_Net  Exposure_Net(%)  NetMktVal  \
240   4.320744e+06             0.0  4.320744e+06         0.245959  4320744.0   

     Capital($)  Capital(%)  BaseCaseNavImpact  OutlierNavImpact       Qty  \
240   4320744.0    0.245959             -15.52            -15.52  181525.0   

    LongShort                  Sector                       Industry  \
240      Long  COMMUNICATION SERVICES  DIVERSIFIED TELECOMMUNICATION   

     CatalystRating CatalystName      Fund_NAV Analyst  Equity_Risk_Exp  \
240               1         Soft  1.756694e+09      SP              0.0   

    DealDuration  
240        0M-3M